# Entendendo como funciona o processamento de texto e áudio de um sistema TTS

# 1) Texto

O texto pode ser processado com base nos fonemas ou com base nos próprios caracteres, aqui trataremos o caso que processa os caracteres.


In [4]:
from src.layers.layers import LinearNorm

In [5]:
from src.layers.layers import ConvNorm, LinearNorm

In [7]:
from src.models.model import LocationLayer

In [1]:
import yaml

In [9]:
import argparse

parser = argparse.ArgumentParser(
    description="Decode dumped features with trained Parallel WaveGAN Generator "
                "(See detail in parallel_wavegan/bin/decode.py).")
parser.add_argument("--config", default=None, type=str,
                    help="yaml format configuration file. if not explicitly provided, "
                         "it will be searched in the checkpoint directory. (default=None)")
args = parser.parse_args()

usage: ipykernel_launcher.py [-h] [--config CONFIG]
ipykernel_launcher.py: error: unrecognized arguments: -f C:\Users\lucas\AppData\Roaming\jupyter\runtime\kernel-56847517-647b-49c2-9e9f-45129dc8c18b.json


SystemExit: 2

In [394]:
# load config
with open('./conf/debugger.yaml') as f:
    config = yaml.load(f, Loader=yaml.Loader)
# config.update(vars(args))

In [395]:
config

{'epochs': 500,
 'iters_per_checkpoint': 1000,
 'seed': 1234,
 'dynamic_loss_scaling': True,
 'fp16_run': False,
 'distributed_run': False,
 'dist_backend': 'nccl',
 'dist_url': 'tcp://localhost:54321',
 'cudnn_enabled': True,
 'cudnn_benchmark': False,
 'ignore_layers': ['embedding.weight']}

In [392]:
config['sampling_rate']

16000

In [5]:
help(config.update)

Help on built-in function update:

update(...) method of builtins.dict instance
    D.update([E, ]**F) -> None.  Update D from dict/iterable E and F.
    If E is present and has a .keys() method, then does:  for k in E: D[k] = E[k]
    If E is present and lacks a .keys() method, then does:  for k, v in E: D[k] = v
    In either case, this is followed by: for k in F:  D[k] = F[k]



In [9]:
import librosa
import IPython.display as ipd
import numpy as np

In [10]:
librosa.__version__

'0.7.2'

In [82]:
# audio, sr_sampled = librosa.load('./data/VCTK/VCTK-Corpus/wav48/p226/p226_003.wav', sr = 16000)
# audio, sr_sampled = librosa.load('./data/VCTK/VCTK-Corpus/wav48/p231/p231_012.wav', sr = 16000)
audio, sr_sampled = librosa.load('./data/VCTK/VCTK-Corpus/wav48/p247/p247_012.wav', sr = 16000)
# audio, sr_sampled = librosa.load('./data/VCTK/VCTK-Corpus/wav48/p257/p257_012.wav', sr = 16000)

In [83]:
sr_sampled

16000

In [84]:
ipd.Audio(audio, rate=sr_sampled)

In [89]:
trim_top_db = 25
n_fft = 1024
hop_length = 124
max_wav_value = 32768.0

data_ = audio.copy()
data_ = librosa.effects.trim(data_, top_db=trim_top_db, frame_length=n_fft, hop_length=hop_length)[0]
data_ = data_
data_ = np.append([0.]*5*hop_length, data_)
data_ = np.append(data_, [0.]*5*hop_length)

In [90]:
ipd.Audio(data_, rate=sr_sampled)

In [38]:
hop_size = 128
win_length = 512
window = 'hann'
num_mels = 80
fft_size = 512
fmin = 0
fmax = 8000
eps = 1e-2
sampling_rate = sr_sampled

In [39]:
x_stft = librosa.stft(audio, n_fft=fft_size, hop_length=hop_size,
                          win_length=win_length, window=window, pad_mode="reflect")

spc = np.abs(x_stft)**2 # (#frames, #bins)
# spc = np.abs(x_stft)

# get mel basis
fmin = 0 if fmin is None else fmin
fmax = sampling_rate / 2 if fmax is None else fmax
print(fmin, fmax)
mel_basis = librosa.filters.mel(sampling_rate, fft_size, num_mels, fmin, fmax)

melspec2 = np.log10(np.maximum(eps, np.dot(mel_basis, spc)))

0 8000


In [40]:
x_stft = librosa.feature.melspectrogram(audio, n_mels = num_mels, n_fft=fft_size, hop_length=hop_size,
                          win_length=win_length, window=window, pad_mode="reflect", fmin=fmin, fmax=fmax, sr = sampling_rate)
melspec = np.log10(x_stft)

In [41]:
dif = melspec - melspec2
dif

array([[-0.02645826, -0.35174656, -0.41901803, ...,  0.        ,
        -0.03772259, -0.58700943],
       [-0.46622825, -0.9364569 , -0.4404111 , ..., -0.03682995,
        -0.2358141 , -0.6636789 ],
       [-1.3377378 , -1.1765568 , -0.9641504 , ..., -1.1053464 ,
        -1.0830889 , -1.3003967 ],
       ...,
       [-4.226833  , -4.7967906 , -5.576277  , ..., -5.7130604 ,
        -5.8643785 , -4.5601926 ],
       [-4.075169  , -4.6658163 , -5.7776847 , ..., -6.185749  ,
        -5.916371  , -4.545405  ],
       [-4.099622  , -4.7001605 , -7.1650543 , ..., -6.9855843 ,
        -6.00747   , -4.447509  ]], dtype=float32)

In [42]:

# audio = librosa.feature.inverse.mel_to_audio(M = np.power(melspec, 10.0), sr = sampling_rate,
#                                             n_fft = fft_size, hop_length = hop_size,
#                                             win_length = win_length, window = window,
#                                             pad_mode='reflect', n_iter = 60, fmin = fmin,
#                                             fmax = fmax)

S = librosa.feature.inverse.mel_to_stft(M = np.power(10.0, melspec), sr = sampling_rate,
                                            n_fft = fft_size,  fmin = fmin,
                                            fmax = fmax, power = 2.0)

y = librosa.griffinlim(S, hop_length = hop_size,
                                            win_length = win_length, window = window,
                                            pad_mode='reflect', n_iter = 60)

In [43]:
ipd.Audio(y, rate=sr_sampled)

In [380]:
ipd.Audio(y, rate=sr_sampled)

In [265]:
# Lendo e passando arquivos pra 16Khz

import scipy.io.wavfile

In [268]:
audio, sr_sampled = librosa.load('./data/VCTK/VCTK-Corpus/wav48/p226/p226_003.wav', sr = 16000)
scipy.io.wavfile.write('p226_003.wav',sr_sampled,audio)
print(sr_sampled)

audio, sr_sampled = librosa.load('./data/VCTK/VCTK-Corpus/wav48/p226/p226_005.wav', sr = 16000)
scipy.io.wavfile.write('p226_005.wav',sr_sampled,audio)
print(sr_sampled)

audio, sr_sampled = librosa.load('./data/VCTK/VCTK-Corpus/wav48/p231/p231_003.wav', sr = 16000)
scipy.io.wavfile.write('p231_003.wav',sr_sampled,audio)
print(sr_sampled)

audio, sr_sampled = librosa.load('./data/VCTK/VCTK-Corpus/wav48/p231/p231_005.wav', sr = 16000)
scipy.io.wavfile.write('p231_005.wav',sr_sampled,audio)
print(sr_sampled)

audio, sr_sampled = librosa.load('./data/VCTK/VCTK-Corpus/wav48/p247/p247_003.wav', sr = 16000)
scipy.io.wavfile.write('p247_003.wav',sr_sampled,audio)
print(sr_sampled)

audio, sr_sampled = librosa.load('./data/VCTK/VCTK-Corpus/wav48/p247/p247_005.wav', sr = 16000)
scipy.io.wavfile.write('p247_005.wav',sr_sampled,audio)
print(sr_sampled)

16000
16000
16000
16000
16000
16000


In [45]:
audio, sr_sampled = librosa.load('./tests/p226_003.wav', sr = 16000)
ipd.Audio(audio, rate=sr_sampled)

In [46]:
len(audio)/sr_sampled

8.3643125

In [281]:
audio, sr_sampled = librosa.load('./tests/p226_003_gen.wav', sr = 16000)
ipd.Audio(audio, rate=sr_sampled)

In [282]:
audio, sr_sampled = librosa.load('./tests/p226_005.wav', sr = 16000)
ipd.Audio(audio, rate=sr_sampled)

In [283]:
audio, sr_sampled = librosa.load('./tests/p226_005_gen.wav', sr = 16000)
ipd.Audio(audio, rate=sr_sampled)

In [284]:
audio, sr_sampled = librosa.load('./tests/p231_003.wav', sr = 16000)
ipd.Audio(audio, rate=sr_sampled)

In [285]:
audio, sr_sampled = librosa.load('./tests/p231_003_gen.wav', sr = 16000)
ipd.Audio(audio, rate=sr_sampled)

In [286]:
audio, sr_sampled = librosa.load('./tests/p247_003.wav', sr = 16000)
ipd.Audio(audio, rate=sr_sampled)

In [288]:
audio, sr_sampled = librosa.load('./tests/p247_003_gen.wav', sr = 16000)
ipd.Audio(audio, rate=sr_sampled)

In [290]:
import h5py
import logging
from utils import write_hdf5

In [333]:
file = 'p247_005'
loc = file[:4]
audio, sr_sampled = librosa.load(f'./data/VCTK/VCTK-Corpus/wav48/{loc}/{file}.wav', sr = 48000)

x_stft = librosa.stft(audio, n_fft=fft_size, hop_length=hop_size,
                          win_length=win_length, window=window, pad_mode="reflect")

# spc = np.abs(x_stft)**2 # (#frames, #bins)
spc = np.abs(x_stft)

# get mel basis
fmin = 0 if fmin is None else fmin
fmax = sampling_rate / 2 if fmax is None else fmax
print(fmin, fmax)
mel_basis = librosa.filters.mel(sampling_rate, fft_size, num_mels, fmin, fmax)

melspec2 = np.log10(np.maximum(eps, np.dot(mel_basis, spc)))

audio = np.pad(audio, (0, fft_size), mode="reflect")
audio = audio[:len(melspec2.T) * hop_size]
assert len(melspec2.T) * hop_size == len(audio)

write_hdf5(f'{file}.h5', 'feats', melspec2.T.astype(np.float32))
write_hdf5(f'{file}.h5', 'wave', audio.astype(np.float32))

0 8000


In [315]:
melspec2.T.shape

(785, 80)

In [335]:
audio, sr_sampled = librosa.load('./ressintese_48k/p226_005_gen.wav', sr = 48000)
ipd.Audio(audio, rate=sr_sampled)

In [405]:
audio, sr_sampled = librosa.load('./data/LJSpeech/LJSpeech-1.1/wavs/LJ001-0001.wav', sr = 22500)

hop_size = 256
win_length = 1024
window = 'hann'
num_mels = 80
fft_size = 1024
fmin = 0
fmax = 8000
eps = 1e-10
sampling_rate = sr_sampled
# x_stft = librosa.stft(audio, n_fft=fft_size, hop_length=hop_size,
#                           win_length=win_length, window=window, pad_mode="reflect")

# spc = np.abs(x_stft)**2 # (#frames, #bins)
# # spc = np.abs(x_stft)

# # get mel basis
# fmin = 0 if fmin is None else fmin
# fmax = sampling_rate / 2 if fmax is None else fmax
# print(fmin, fmax)
# mel_basis = librosa.filters.mel(sampling_rate, fft_size, num_mels, fmin, fmax)

# melspec2 = np.log10(np.maximum(eps, np.dot(mel_basis, spc)))

x_stft = librosa.feature.melspectrogram(audio, n_mels = num_mels, n_fft=fft_size, hop_length=hop_size,
                          win_length=win_length, window=window, pad_mode="reflect", fmin=fmin, fmax=fmax, sr = sampling_rate)
melspec = np.log10(x_stft)

# audio = librosa.feature.inverse.mel_to_audio(M = np.power(melspec, 10.0), sr = sampling_rate,
#                                             n_fft = fft_size, hop_length = hop_size,
#                                             win_length = win_length, window = window,
#                                             pad_mode='reflect', n_iter = 60, fmin = fmin,
#                                             fmax = fmax)

S = librosa.feature.inverse.mel_to_stft(M = np.power(10.0, melspec), sr = sampling_rate,
                                            n_fft = fft_size,  fmin = fmin,
                                            fmax = fmax, power = 2.0)

In [406]:
y = librosa.griffinlim(S, hop_length = hop_size,
                                            win_length = win_length, window = window,
                                            pad_mode='reflect', n_iter = 100)

ipd.Audio(y, rate=sr_sampled)